Code from GitHub: https://github.com/rkcosmos/deepcut

In [1]:
import onnxruntime as ort
import numpy as np

In [19]:
import onnx
onnx_model = onnx.load("model.onnx")
onnx.checker.check_model(onnx_model)
print([input.name for input in onnx_model.graph.input])
print([output.name for output in onnx_model.graph.output])

['input_1', 'input_2']
['dense_13']


In [21]:
initializer_names = {initializer.name for initializer in onnx_model.graph.initializer}
input_names = [input.name for input in onnx_model.graph.input if input.name not in initializer_names]

In [23]:
initializer_names

{'Func/StatefulPartitionedCall/input/_2:0',
 'Func/StatefulPartitionedCall/input/_55:0',
 'StatefulPartitionedCall/model/batch_normalization/batchnorm/mul:0',
 'StatefulPartitionedCall/model/batch_normalization/batchnorm/sub:0',
 'StatefulPartitionedCall/model/batch_normalization_1/batchnorm/mul:0',
 'StatefulPartitionedCall/model/batch_normalization_1/batchnorm/sub:0',
 'StatefulPartitionedCall/model/conv1d/conv1d/ExpandDims_1:0',
 'StatefulPartitionedCall/model/conv1d_1/conv1d/ExpandDims_1:0',
 'StatefulPartitionedCall/model/conv1d_10/conv1d/ExpandDims_1:0',
 'StatefulPartitionedCall/model/conv1d_11/conv1d/ExpandDims_1:0',
 'StatefulPartitionedCall/model/conv1d_2/conv1d/ExpandDims_1:0',
 'StatefulPartitionedCall/model/conv1d_3/conv1d/ExpandDims_1:0',
 'StatefulPartitionedCall/model/conv1d_4/conv1d/ExpandDims_1:0',
 'StatefulPartitionedCall/model/conv1d_5/conv1d/ExpandDims_1:0',
 'StatefulPartitionedCall/model/conv1d_6/conv1d/ExpandDims_1:0',
 'StatefulPartitionedCall/model/conv1d_7/c

In [15]:
onnx_model

ir_version: 7
producer_name: "tf2onnx"
producer_version: "1.12.0 ddca3a"
graph {
  node {
    input: "input_2"
    output: "StatefulPartitionedCall/model/embedding_1/Cast:0"
    name: "StatefulPartitionedCall/model/embedding_1/Cast"
    op_type: "Cast"
    attribute {
      name: "to"
      i: 6
      type: INT
    }
  }
  node {
    input: "input_1"
    output: "StatefulPartitionedCall/model/embedding/Cast:0"
    name: "StatefulPartitionedCall/model/embedding/Cast"
    op_type: "Cast"
    attribute {
      name: "to"
      i: 6
      type: INT
    }
  }
  node {
    input: "Func/StatefulPartitionedCall/input/_55:0"
    input: "StatefulPartitionedCall/model/embedding_1/Cast:0"
    output: "StatefulPartitionedCall/model/embedding_1/embedding_lookup:0"
    name: "StatefulPartitionedCall/model/embedding_1/embedding_lookup"
    op_type: "Gather"
    attribute {
      name: "axis"
      i: 0
      type: INT
    }
  }
  node {
    input: "Func/StatefulPartitionedCall/input/_2:0"
    input: "

In [2]:
ort_sess = ort.InferenceSession('model.onnx')

In [24]:
input_name = ort_sess.get_inputs()[0].name
print("input name", input_name)
input_shape = ort_sess.get_inputs()[0].shape
print("input shape", input_shape)
input_type = ort_sess.get_inputs()[0].type
print("input type", input_type)

input name input_1
input shape ['unk__330', 21]
input type tensor(float)


In [26]:
input_name = ort_sess.get_inputs()[1].name
print("input name", input_name)
input_shape = ort_sess.get_inputs()[1].shape
print("input shape", input_shape)
input_type = ort_sess.get_inputs()[1].type
print("input type", input_type)

input name input_2
input shape ['unk__331', 21]
input type tensor(float)


In [11]:
ort_sess.get_inputs()

In [8]:
dir(ort_sess)

['__class__',
 '__delattr__',
 '__dict__',
 '__dir__',
 '__doc__',
 '__eq__',
 '__format__',
 '__ge__',
 '__getattribute__',
 '__gt__',
 '__hash__',
 '__init__',
 '__init_subclass__',
 '__le__',
 '__lt__',
 '__module__',
 '__ne__',
 '__new__',
 '__reduce__',
 '__reduce_ex__',
 '__repr__',
 '__setattr__',
 '__sizeof__',
 '__str__',
 '__subclasshook__',
 '__weakref__',
 '_create_inference_session',
 '_enable_fallback',
 '_fallback_providers',
 '_inputs_meta',
 '_model_bytes',
 '_model_meta',
 '_model_path',
 '_outputs_meta',
 '_overridable_initializers',
 '_profiling_start_time_ns',
 '_provider_options',
 '_providers',
 '_read_config_from_model',
 '_reset_session',
 '_sess',
 '_sess_options',
 '_sess_options_initial',
 'disable_fallback',
 'enable_fallback',
 'end_profiling',
 'get_inputs',
 'get_modelmeta',
 'get_outputs',
 'get_overridable_initializers',
 'get_profiling_start_time_ns',
 'get_provider_options',
 'get_providers',
 'get_session_options',
 'io_binding',
 'run',
 'run_with_

In [4]:
from deepcut.utils import CHAR_TYPES_MAP, CHARS_MAP, create_feature_array

/opt/conda/lib/python3.8/site-packages/scipy/__init__.py:146: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.23.4
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"
2022-10-28 10:46:31.337759: I tensorflow/stream_executor/platform/default/dso_loader.cc:49] Successfully opened dynamic library libcudart.so.11.0


In [5]:
n_pad = 21

In [6]:
text="ทดสอบการตัดคำภาษาไทยครับ"

In [7]:
x_char, x_type = create_feature_array(text, n_pad=n_pad)

In [29]:
x_char.shape

(24, 21)

In [37]:
x_char=x_char.astype(np.float32)
x_type=x_type.astype(np.float32)

In [39]:
outputs = ort_sess.run(None, {'input_1': x_char, 'input_2':x_type})

In [40]:
outputs

[array([[0.99999595],
        [0.        ],
        [0.00146589],
        [0.00179249],
        [0.        ],
        [0.99891174],
        [0.        ],
        [0.        ],
        [0.9998429 ],
        [0.        ],
        [0.        ],
        [0.95358664],
        [0.        ],
        [0.99998593],
        [0.        ],
        [0.        ],
        [0.        ],
        [0.9999982 ],
        [0.        ],
        [0.        ],
        [0.9975493 ],
        [0.        ],
        [0.        ],
        [0.        ]], dtype=float32)]

In [44]:
y_predict = (outputs[0].ravel() > 0.5).astype(int)
word_end = y_predict[1:].tolist() + [1]

In [45]:
def tokenize(text):
        x_char, x_type = create_feature_array(text, n_pad=n_pad)
        x_char=x_char.astype(np.float32)
        x_type=x_type.astype(np.float32)
        outputs = ort_sess.run(None, {'input_1': x_char, 'input_2':x_type})
        y_predict = (outputs[0].ravel() > 0.5).astype(int)
        word_end = y_predict[1:].tolist() + [1]
        tokens = []
        word = ''
        for char, w_e in zip(text, word_end):
            word += char
            if w_e:
                tokens.append(word)
                word = ''
        return tokens

In [46]:
tokenize(text)

['ทดสอบ', 'การ', 'ตัด', 'คำ', 'ภาษา', 'ไทย', 'ครับ']